# only Person, location, Organzation

In [1]:
%load_ext autoreload
%autoreload 2

In [1]:
from transformers import pipeline, AutoTokenizer, AutoModelForTokenClassification
from transformers import AutoModelForTokenClassification
from span_marker import SpanMarkerModel
import re

from data_manipulation.dataset_funcions import create_cnec_dataset
from evaluation_functions import evaluate_test_model, get_result_as_tables


ImportError: cannot import name 'gazetteer_matching' from partially initialized module 'data_manipulation.dataset_funcions' (most likely due to a circular import) (/home/xstromp/dp/ner/data_manipulation/dataset_funcions.py)

# Dataset

In [3]:
id2label = {
    0: "O",
    1: "B-PER",
    2: "I-PER",
    3: "B-ORG",
    4: "I-ORG",
    5: "B-LOC",
    6: "I-LOC",
}
label2id = {v: k for k, v in id2label.items()}
label_list = sorted(list(label2id.keys()), key=len, reverse=True)
shorted_label_list = sorted(list(set([x.replace("B-", "I-") for x in label_list])), key=len, reverse=True)
label_list, shorted_label_list

(['B-PER', 'I-PER', 'B-ORG', 'I-ORG', 'B-LOC', 'I-LOC', 'O'],
 ['I-LOC', 'I-PER', 'I-ORG', 'O'])

In [5]:
label_mapper_cnec = {
    "p": 1,
#     "mn": 2,
    "i": 2,
    "g": 3
}
raw_dataset = create_cnec_dataset(label_mapper_cnec)
raw_dataset

100%|██████████| 902/902 [00:00<00:00, 14584.55it/s]


DatasetDict({
    train: Dataset({
        features: ['id', 'tokens', 'ner_tags', 'sentence'],
        num_rows: 7193
    })
    validation: Dataset({
        features: ['id', 'tokens', 'ner_tags', 'sentence'],
        num_rows: 899
    })
    test: Dataset({
        features: ['id', 'tokens', 'ner_tags', 'sentence'],
        num_rows: 900
    })
})

In [4]:
def tokenize_dataset(tokenizer):
    def tokenize_and_align_labels(examples):
        tokenized_inputs = tokenizer(examples["tokens"], truncation=True, is_split_into_words=True)

        labels = []
        for i, label in enumerate(examples[f"ner_tags"]):
            word_ids = tokenized_inputs.word_ids(batch_index=i)  # Map tokens to their respective word.
            previous_word_idx = None
            label_ids = []
            for word_idx in word_ids:  # Set the special tokens to -100.
                if word_idx is None:
                    label_ids.append(-100)
                elif word_idx != previous_word_idx:  # Only label the first token of a given word.
                    label_ids.append(label[word_idx])
                else:
                    label_ids.append(-100)
                previous_word_idx = word_idx
            labels.append(label_ids)

        tokenized_inputs["labels"] = labels
        return tokenized_inputs

    dataset = raw_dataset.map(tokenize_and_align_labels, batched=True)
    return dataset

# Models

In [7]:
def process_predictions(prediction, mid_result_for_word, label2id, sentence_counter, word):
    if  prediction["start"] > sentence_counter and prediction["end"] <= sentence_counter + len(word) + 1:
        score = mid_result_for_word[label2id.get(prediction["entity"], 0)]
        mid_result_for_word[label2id.get(prediction["entity"], 0)] = score +  prediction["score"]
    return mid_result_for_word

### stulcrad/CNEC_extended_xlm-roberta-large
https://huggingface.co/stulcrad/CNEC_extended_xlm-roberta-large

In [8]:
def fcnec_ger_ner_tag(text):
    text = str(text)
    if "P" in text:
        return text[:2] + "PER"
    if "G" in text:
        return text[:2] + "LOC"
    if "-I" in text:
        return text[:2] + "ORG"    
    # if "M" in text:
    #     return text[:2] + "ORG"
    return "O"
        
def process_predictions_cnec(prediction, mid_result_for_word, label2id, sentence_counter, word):
    if  prediction["start"] > sentence_counter and prediction["end"] <= sentence_counter + len(word) + 1:
        score = mid_result_for_word[label2id.get(fcnec_ger_ner_tag(prediction["entity"]), 0)]
        mid_result_for_word[label2id.get(fcnec_ger_ner_tag(prediction["entity"]), 0)] = score +  prediction["score"]
    return mid_result_for_word
model_name = "stulcrad/CNEC_extended_xlm-roberta-large"
tokenizer = AutoTokenizer.from_pretrained(model_name)
dataset = tokenize_dataset(tokenizer)
model = AutoModelForTokenClassification.from_pretrained(model_name)

results, results_by_tag, data_for_cm = evaluate_test_model(model, tokenizer, dataset["test"], id2label, process_predictions=process_predictions_cnec)

Map:   0%|          | 0/7193 [00:00<?, ? examples/s]

Map:   0%|          | 0/899 [00:00<?, ? examples/s]

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

100%|██████████| 900/900 [02:45<00:00,  5.45it/s]


In [9]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,8893838158871566; 0,9220489977728286; 0,8455827765404602; 0,8975501113585747]
   Metric    ent_type     partial      strict       exact
  correct 1198.000000 1209.000000 1139.000000 1209.000000
incorrect   77.000000    0.000000  136.000000   66.000000
  partial    0.000000   66.000000    0.000000    0.000000
   missed   75.000000   75.000000   75.000000   75.000000
 spurious   69.000000   69.000000   69.000000   69.000000
 possible 1350.000000 1350.000000 1350.000000 1350.000000
   actual 1344.000000 1344.000000 1344.000000 1344.000000
precision    0.891369    0.924107    0.847470    0.899554
   recall    0.887407    0.920000    0.843704    0.895556
       f1    0.889384    0.922049    0.845583    0.897550


### 51la5/roberta-large-NER
https://huggingface.co/51la5/roberta-large-NER

In [13]:
model_name = "51la5/roberta-large-NER"
tokenizer = AutoTokenizer.from_pretrained(model_name)
dataset = tokenize_dataset(tokenizer)
model = AutoModelForTokenClassification.from_pretrained(model_name)
results, results_by_tag, data_for_cm = evaluate_test_model(model, tokenizer, dataset["test"], id2label, process_predictions=process_predictions)

Map:   0%|          | 0/7193 [00:00<?, ? examples/s]

Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


Map:   0%|          | 0/899 [00:00<?, ? examples/s]

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

Some weights of the model checkpoint at 51la5/roberta-large-NER were not used when initializing XLMRobertaForTokenClassification: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing XLMRobertaForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
100%|██████████| 900/900 [02:52<00:00,  5.22it/s]


In [14]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,8110065170166545; 0,8580738595220855; 0,7487328023171614; 0,8189717595944968]
   Metric    ent_type     partial      strict       exact
  correct 1120.000000 1131.000000 1034.000000 1131.000000
incorrect  119.000000    0.000000  205.000000  108.000000
  partial    0.000000  108.000000    0.000000    0.000000
   missed  111.000000  111.000000  111.000000  111.000000
 spurious  173.000000  173.000000  173.000000  173.000000
 possible 1350.000000 1350.000000 1350.000000 1350.000000
   actual 1412.000000 1412.000000 1412.000000 1412.000000
precision    0.793201    0.839235    0.732295    0.800992
   recall    0.829630    0.877778    0.765926    0.837778
       f1    0.811007    0.858074    0.748733    0.818972


### Babelscape/wikineural-multilingual-ner
https://huggingface.co/Babelscape/wikineural-multilingual-ner

In [15]:
model_name = "Babelscape/wikineural-multilingual-ner"
tokenizer = AutoTokenizer.from_pretrained(model_name)
dataset = tokenize_dataset(tokenizer)
model = AutoModelForTokenClassification.from_pretrained(model_name).to("cuda")
results, results_by_tag, data_for_cm = evaluate_test_model(model, tokenizer, dataset["test"], id2label, process_predictions=process_predictions)

tokenizer_config.json:   0%|          | 0.00/333 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/996k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.96M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

Map:   0%|          | 0/7193 [00:00<?, ? examples/s]

Map:   0%|          | 0/899 [00:00<?, ? examples/s]

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

config.json:   0%|          | 0.00/1.19k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/709M [00:00<?, ?B/s]

100%|██████████| 900/900 [00:55<00:00, 16.24it/s]


In [16]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)


[0,7887751232461129; 0,8426241941600303; 0,7417519908987485; 0,8115282518012894]
   Metric    ent_type     partial      strict       exact
  correct 1040.000000 1070.000000  978.000000 1070.000000
incorrect  112.000000    0.000000  174.000000   82.000000
  partial    0.000000   82.000000    0.000000    0.000000
   missed  197.000000  197.000000  197.000000  197.000000
 spurious  136.000000  136.000000  136.000000  136.000000
 possible 1349.000000 1349.000000 1349.000000 1349.000000
   actual 1288.000000 1288.000000 1288.000000 1288.000000
precision    0.807453    0.862578    0.759317    0.830745
   recall    0.770941    0.823573    0.724981    0.793180
       f1    0.788775    0.842624    0.741752    0.811528


### FacebookAI/xlm-roberta-large-finetuned-conll03-english
https://huggingface.co/FacebookAI/xlm-roberta-large-finetuned-conll03-english

In [19]:
model_name = "xlm-roberta-large-finetuned-conll03-english"
tokenizer = AutoTokenizer.from_pretrained(model_name)
dataset = tokenize_dataset(tokenizer)
model = AutoModelForTokenClassification.from_pretrained(model_name).to("cuda")
results, results_by_tag, data_for_cm = evaluate_test_model(model, tokenizer, dataset["test"], id2label, process_predictions=process_predictions)

tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/852 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.10M [00:00<?, ?B/s]

Map:   0%|          | 0/7193 [00:00<?, ? examples/s]

Map:   0%|          | 0/899 [00:00<?, ? examples/s]

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

model.safetensors:   0%|          | 0.00/2.24G [00:00<?, ?B/s]

Some weights of the model checkpoint at xlm-roberta-large-finetuned-conll03-english were not used when initializing XLMRobertaForTokenClassification: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing XLMRobertaForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
100%|██████████| 900/900 [02:44<00:00,  5.47it/s]


In [20]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,8110065170166545; 0,8580738595220855; 0,7487328023171614; 0,8189717595944968]
   Metric    ent_type     partial      strict       exact
  correct 1120.000000 1131.000000 1034.000000 1131.000000
incorrect  119.000000    0.000000  205.000000  108.000000
  partial    0.000000  108.000000    0.000000    0.000000
   missed  111.000000  111.000000  111.000000  111.000000
 spurious  173.000000  173.000000  173.000000  173.000000
 possible 1350.000000 1350.000000 1350.000000 1350.000000
   actual 1412.000000 1412.000000 1412.000000 1412.000000
precision    0.793201    0.839235    0.732295    0.800992
   recall    0.829630    0.877778    0.765926    0.837778
       f1    0.811007    0.858074    0.748733    0.818972


### dslim/bert-base-NER
https://huggingface.co/dslim/bert-base-NER

In [17]:
model_name = "dslim/bert-base-NER"
tokenizer = AutoTokenizer.from_pretrained(model_name)
dataset = tokenize_dataset(tokenizer)
model = AutoModelForTokenClassification.from_pretrained(model_name).to("cuda")
results, results_by_tag, data_for_cm = evaluate_test_model(model, tokenizer, dataset["test"], id2label, process_predictions=process_predictions)


tokenizer_config.json:   0%|          | 0.00/59.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/829 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/213k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/2.00 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

Map:   0%|          | 0/7193 [00:00<?, ? examples/s]

Map:   0%|          | 0/899 [00:00<?, ? examples/s]

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

model.safetensors:   0%|          | 0.00/433M [00:00<?, ?B/s]

Some weights of the model checkpoint at dslim/bert-base-NER were not used when initializing BertForTokenClassification: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
100%|██████████| 900/900 [01:11<00:00, 12.62it/s]


In [18]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,3372851215174867; 0,5619442797866034; 0,23355068168346177; 0,45287492590397155]
   Metric    ent_type     partial      strict       exact
  correct  569.000000  764.000000  394.000000  764.000000
incorrect  563.000000    0.000000  738.000000  368.000000
  partial    0.000000  368.000000    0.000000    0.000000
   missed  206.000000  206.000000  206.000000  206.000000
 spurious  904.000000  904.000000  904.000000  904.000000
 possible 1338.000000 1338.000000 1338.000000 1338.000000
   actual 2036.000000 2036.000000 2036.000000 2036.000000
precision    0.279470    0.465619    0.193517    0.375246
   recall    0.425262    0.708520    0.294469    0.571001
       f1    0.337285    0.561944    0.233551    0.452875


### orgcatorg/bert-base-multilingual-cased-ner
https://huggingface.co/orgcatorg/bert-base-multilingual-cased-ner

In [21]:
model_name = "orgcatorg/bert-base-multilingual-cased-ner"
tokenizer = AutoTokenizer.from_pretrained(model_name)
dataset = tokenize_dataset(tokenizer)
model = AutoModelForTokenClassification.from_pretrained(model_name).to("cuda")
results, results_by_tag, data_for_cm = evaluate_test_model(model, tokenizer, dataset["test"], id2label, process_predictions=process_predictions)

tokenizer_config.json:   0%|          | 0.00/1.19k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/996k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.92M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

Map:   0%|          | 0/7193 [00:00<?, ? examples/s]

Map:   0%|          | 0/899 [00:00<?, ? examples/s]

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

config.json:   0%|          | 0.00/1.11k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/709M [00:00<?, ?B/s]

100%|██████████| 900/900 [01:01<00:00, 14.58it/s]


In [22]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,5340909090909092; 0,5873205741626794; 0,4521531100478469; 0,5245215311004785]
   Metric    ent_type     partial      strict       exact
  correct  893.000000  877.000000  756.000000  877.000000
incorrect  194.000000    0.000000  331.000000  210.000000
  partial    0.000000  210.000000    0.000000    0.000000
   missed  262.000000  262.000000  262.000000  262.000000
 spurious  908.000000  908.000000  908.000000  908.000000
 possible 1349.000000 1349.000000 1349.000000 1349.000000
   actual 1995.000000 1995.000000 1995.000000 1995.000000
precision    0.447619    0.492231    0.378947    0.439599
   recall    0.661972    0.727947    0.560415    0.650111
       f1    0.534091    0.587321    0.452153    0.524522


### orgcatorg/distilbert-base-multilingual-cased-ner
https://huggingface.co/orgcatorg/distilbert-base-multilingual-cased-ner

In [23]:
model_name = "orgcatorg/distilbert-base-multilingual-cased-ner"
tokenizer = AutoTokenizer.from_pretrained(model_name)
dataset = tokenize_dataset(tokenizer)
model = AutoModelForTokenClassification.from_pretrained(model_name).to("cuda")
results, results_by_tag, data_for_cm = evaluate_test_model(model, tokenizer, dataset["test"], id2label, process_predictions=process_predictions)

tokenizer_config.json:   0%|          | 0.00/1.23k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/996k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.92M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

Map:   0%|          | 0/7193 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/899 [00:00<?, ? examples/s]

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

config.json:   0%|          | 0.00/879 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/539M [00:00<?, ?B/s]

100%|██████████| 900/900 [00:31<00:00, 28.74it/s]


In [24]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,48771825984018946; 0,5495708789582717; 0,40071026931044684; 0,4794317845516425]
   Metric    ent_type     partial      strict       exact
  correct  824.000000  810.000000  677.000000  810.000000
incorrect  223.000000    0.000000  370.000000  237.000000
  partial    0.000000  237.000000    0.000000    0.000000
   missed  299.000000  299.000000  299.000000  299.000000
 spurious  986.000000  986.000000  986.000000  986.000000
 possible 1346.000000 1346.000000 1346.000000 1346.000000
   actual 2033.000000 2033.000000 2033.000000 2033.000000
precision    0.405312    0.456714    0.333005    0.398426
   recall    0.612184    0.689822    0.502972    0.601783
       f1    0.487718    0.549571    0.400710    0.479432


### gunghio/distilbert-base-multilingual-cased-finetuned-conll2003-ner
https://huggingface.co/gunghio/distilbert-base-multilingual-cased-finetuned-conll2003-ner

In [25]:
model_name = "gunghio/distilbert-base-multilingual-cased-finetuned-conll2003-ner"
tokenizer = AutoTokenizer.from_pretrained(model_name)
dataset = tokenize_dataset(tokenizer)
model = AutoModelForTokenClassification.from_pretrained(model_name).to("cuda")
results, results_by_tag, data_for_cm = evaluate_test_model(model, tokenizer, dataset["test"], id2label, process_predictions=process_predictions)

tokenizer_config.json:   0%|          | 0.00/303 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/911 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/996k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.96M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

Map:   0%|          | 0/7193 [00:00<?, ? examples/s]

Map:   0%|          | 0/899 [00:00<?, ? examples/s]

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

pytorch_model.bin:   0%|          | 0.00/539M [00:00<?, ?B/s]

100%|██████████| 900/900 [00:36<00:00, 24.35it/s]


In [26]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,6495564005069709; 0,7458808618504436; 0,5519645120405577; 0,6799746514575412]
   Metric    ent_type     partial      strict       exact
  correct 1025.000000 1073.000000  871.000000 1073.000000
incorrect  256.000000    0.000000  410.000000  208.000000
  partial    0.000000  208.000000    0.000000    0.000000
   missed   70.000000   70.000000   70.000000   70.000000
 spurious  524.000000  524.000000  524.000000  524.000000
 possible 1351.000000 1351.000000 1351.000000 1351.000000
   actual 1805.000000 1805.000000 1805.000000 1805.000000
precision    0.567867    0.652078    0.482548    0.594460
   recall    0.758697    0.871207    0.644708    0.794226
       f1    0.649556    0.745881    0.551965    0.679975


### sagorsarker/codeswitch-spaeng-ner-lince
https://huggingface.co/sagorsarker/codeswitch-spaeng-ner-lince

In [31]:
model_name = "sagorsarker/codeswitch-spaeng-ner-lince"
tokenizer = AutoTokenizer.from_pretrained(model_name)
dataset = tokenize_dataset(tokenizer)
model = AutoModelForTokenClassification.from_pretrained(model_name).to("cuda")
results, results_by_tag, data_for_cm = evaluate_test_model(model, tokenizer, dataset["test"], id2label, process_predictions=process_predictions)

tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.41k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/996k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

Map:   0%|          | 0/7193 [00:00<?, ? examples/s]

Map:   0%|          | 0/899 [00:00<?, ? examples/s]

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

model.safetensors:   0%|          | 0.00/711M [00:00<?, ?B/s]

Some weights of the model checkpoint at sagorsarker/codeswitch-spaeng-ner-lince were not used when initializing BertForTokenClassification: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
100%|██████████| 900/900 [00:53<00:00, 16.70it/s]


In [32]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,7310664605873262; 0,7299072642967543; 0,6406491499227204; 0,6707882534775889]
   Metric    ent_type     partial      strict       exact
  correct  946.000000  868.000000  829.000000  868.000000
incorrect   75.000000    0.000000  192.000000  153.000000
  partial    0.000000  153.000000    0.000000    0.000000
   missed  315.000000  315.000000  315.000000  315.000000
 spurious  231.000000  231.000000  231.000000  231.000000
 possible 1336.000000 1336.000000 1336.000000 1336.000000
   actual 1252.000000 1252.000000 1252.000000 1252.000000
precision    0.755591    0.754393    0.662141    0.693291
   recall    0.708084    0.706961    0.620509    0.649701
       f1    0.731066    0.729907    0.640649    0.670788


### vesteinn/XLMR-ENIS-finetuned-ner
https://huggingface.co/vesteinn/XLMR-ENIS-finetuned-ner

In [36]:
model_name = "vesteinn/XLMR-ENIS-finetuned-ner"
tokenizer = AutoTokenizer.from_pretrained(model_name)
dataset = tokenize_dataset(tokenizer)
model = AutoModelForTokenClassification.from_pretrained(model_name).to("cuda")
results, results_by_tag, data_for_cm = evaluate_test_model(model, tokenizer, dataset["test"], id2label, process_predictions=process_predictions)

tokenizer_config.json:   0%|          | 0.00/540 [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.14M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/150 [00:00<?, ?B/s]

Map:   0%|          | 0/7193 [00:00<?, ? examples/s]

Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


Map:   0%|          | 0/899 [00:00<?, ? examples/s]

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

config.json:   0%|          | 0.00/1.08k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/495M [00:00<?, ?B/s]

100%|██████████| 900/900 [00:59<00:00, 15.04it/s]


In [37]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,23504574243490498; 0,4522636640863242; 0,14449917898193762; 0,34201266713581985]
   Metric    ent_type     partial      strict       exact
  correct  501.000000  729.000000  308.000000  729.000000
incorrect  698.000000    0.000000  891.000000  470.000000
  partial    0.000000  470.000000    0.000000    0.000000
   missed  151.000000  151.000000  151.000000  151.000000
 spurious 1714.000000 1714.000000 1714.000000 1714.000000
 possible 1350.000000 1350.000000 1350.000000 1350.000000
   actual 2913.000000 2913.000000 2913.000000 2913.000000
precision    0.171988    0.330930    0.105733    0.250257
   recall    0.371111    0.714074    0.228148    0.540000
       f1    0.235046    0.452264    0.144499    0.342013


### rollerhafeezh-amikom/xlm-roberta-base-ner-silvanus
https://huggingface.co/rollerhafeezh-amikom/xlm-roberta-base-ner-silvanus

In [27]:
model_name = "rollerhafeezh-amikom/xlm-roberta-base-ner-silvanus"
tokenizer = AutoTokenizer.from_pretrained(model_name)
dataset = tokenize_dataset(tokenizer)
model = AutoModelForTokenClassification.from_pretrained(model_name).to("cuda")
results, results_by_tag, data_for_cm = evaluate_test_model(model, tokenizer, dataset["test"], id2label, process_predictions=process_predictions)

tokenizer_config.json:   0%|          | 0.00/1.15k [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.1M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/280 [00:00<?, ?B/s]

Map:   0%|          | 0/7193 [00:00<?, ? examples/s]

Map:   0%|          | 0/899 [00:00<?, ? examples/s]

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

config.json:   0%|          | 0.00/988 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.11G [00:00<?, ?B/s]

100%|██████████| 900/900 [00:58<00:00, 15.28it/s]


In [28]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,5062857142857142; 0,5588571428571428; 0,41714285714285715; 0,4857142857142857]
   Metric    ent_type     partial      strict       exact
  correct  443.000000  425.000000  365.000000  425.000000
incorrect  110.000000    0.000000  188.000000  128.000000
  partial    0.000000  128.000000    0.000000    0.000000
   missed  540.000000  540.000000  540.000000  540.000000
 spurious  104.000000  104.000000  104.000000  104.000000
 possible 1093.000000 1093.000000 1093.000000 1093.000000
   actual  657.000000  657.000000  657.000000  657.000000
precision    0.674277    0.744292    0.555556    0.646880
   recall    0.405306    0.447392    0.333943    0.388838
       f1    0.506286    0.558857    0.417143    0.485714


### SpanMarker


In [29]:
def process_predictions_span(prediction, mid_result_for_word, label2id, sentence_counter, word):
    if  prediction["char_start_index"] > sentence_counter and prediction["char_end_index"] <= sentence_counter + len(word) + 1:
        score = mid_result_for_word[label2id.get("B-" + prediction["label"], 0)]
        mid_result_for_word[label2id.get("B-" + prediction["label"], 0)] = score +  prediction["score"]
    return mid_result_for_word
span_marker_model = SpanMarkerModel.from_pretrained("tomaarsen/span-marker-mbert-base-multinerd").to("cuda")
def predict_span(text):
    return span_marker_model.predict(text)
results, results_by_tag, data_for_cm = evaluate_test_model(None, None, dataset["test"], id2label, process_predictions_span, predict_span)

config.json:   0%|          | 0.00/5.08k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/712M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/625 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/996k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.96M [00:00<?, ?B/s]

100%|██████████| 900/900 [08:31<00:00,  1.76it/s]


In [30]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,5033522434244456; 0,5466735430634347; 0,49406910778751933; 0,5394533264569367]
   Metric    ent_type     partial      strict       exact
  correct  488.000000  523.000000  479.000000  523.000000
incorrect   49.000000    0.000000   58.000000   14.000000
  partial    0.000000   14.000000    0.000000    0.000000
   missed  808.000000  808.000000  808.000000  808.000000
 spurious   57.000000   57.000000   57.000000   57.000000
 possible 1345.000000 1345.000000 1345.000000 1345.000000
   actual  594.000000  594.000000  594.000000  594.000000
precision    0.821549    0.892256    0.806397    0.880471
   recall    0.362825    0.394052    0.356134    0.388848
       f1    0.503352    0.546674    0.494069    0.539453


### Flair

In [33]:
from flair.data import Sentence
from flair.models import SequenceTagger
def flair_ger_ner_tag(text):
    text = str(text)
    for label in ["PER", "LOC", "ORG"]:
        if label in text:
            return "B-" + label

In [34]:
def process_predictions_flair(prediction, mid_result_for_word, label2id, sentence_counter, word):
    if  prediction.start_position > sentence_counter and prediction.end_position <= sentence_counter + len(word) + 1:
        score = mid_result_for_word[label2id.get(flair_ger_ner_tag(prediction), 0)]
        match = re.search(r'\((\d+\.\d+)\)', str(prediction))
        if match:
            pred_score = float(match.group(1))
        else:
            print("error")
        mid_result_for_word[label2id.get(flair_ger_ner_tag(prediction), 0)] = score +  pred_score
    return mid_result_for_word
tagger = SequenceTagger.load("flair/ner-multi")
def predict_flair(text):
    sentence = Sentence(text)
    tagger.predict(sentence)
    return sentence.get_spans('ner')
results, results_by_tag, data_for_cm = evaluate_test_model(None, None, dataset["test"], id2label, process_predictions_flair, predict_flair)

2024-04-22 00:52:59,547 SequenceTagger predicts: Dictionary with 20 tags: <unk>, O, B-PER, E-PER, S-LOC, B-MISC, I-MISC, E-MISC, S-PER, B-ORG, E-ORG, S-ORG, I-ORG, B-LOC, E-LOC, S-MISC, I-PER, I-LOC, <START>, <STOP>


100%|██████████| 900/900 [08:19<00:00,  1.80it/s]


In [35]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,3282442748091603; 0,5675572519083969; 0,2564885496183207; 0,5114503816793893]
   Metric    ent_type     partial      strict       exact
  correct  430.000000  670.000000  336.000000  670.000000
incorrect  387.000000    0.000000  481.000000  147.000000
  partial    0.000000  147.000000    0.000000    0.000000
   missed  530.000000  530.000000  530.000000  530.000000
 spurious  456.000000  456.000000  456.000000  456.000000
 possible 1347.000000 1347.000000 1347.000000 1347.000000
   actual 1273.000000 1273.000000 1273.000000 1273.000000
precision    0.337785    0.584053    0.263943    0.526316
   recall    0.319228    0.551967    0.249443    0.497402
       f1    0.328244    0.567557    0.256489    0.511450


### Andrija/SRoBERTa-XL-NER
https://huggingface.co/Andrija/SRoBERTa-XL-NER

In [38]:
def process_predictions_andrija(prediction, mid_result_for_word, label2id, sentence_counter, word):
    if  prediction["start"] > sentence_counter and prediction["end"] <= sentence_counter + len(word) + 1:
        score = mid_result_for_word[label2id.get(prediction["entity"].upper(), 0)]
        mid_result_for_word[label2id.get(prediction["entity"].upper(), 0)] = score +  prediction["score"]
    return mid_result_for_word
model_name = "Andrija/SRoBERTa-XL-NER"
tokenizer = AutoTokenizer.from_pretrained(model_name)
dataset = tokenize_dataset(tokenizer)
model = AutoModelForTokenClassification.from_pretrained(model_name).to("cuda")
results, results_by_tag, data_for_cm = evaluate_test_model(model, tokenizer, dataset["test"], id2label, process_predictions_andrija)


tokenizer_config.json:   0%|          | 0.00/1.12k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.02M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/694k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.81M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/772 [00:00<?, ?B/s]

...

Map:   0%|          | 0/899 [00:00<?, ? examples/s]

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

config.json:   0%|          | 0.00/1.16k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/319M [00:00<?, ?B/s]

100%|██████████| 900/900 [00:33<00:00, 26.86it/s]


In [39]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,5389221556886227; 0,6646706586826348; 0,42381902860944776; 0,5715236194278109]
   Metric    ent_type     partial      strict       exact
  correct  810.000000  859.000000  637.000000  859.000000
incorrect  329.000000    0.000000  502.000000  280.000000
  partial    0.000000  280.000000    0.000000    0.000000
   missed  177.000000  177.000000  177.000000  177.000000
 spurious  551.000000  551.000000  551.000000  551.000000
 possible 1316.000000 1316.000000 1316.000000 1316.000000
   actual 1690.000000 1690.000000 1690.000000 1690.000000
precision    0.479290    0.591124    0.376923    0.508284
   recall    0.615502    0.759119    0.484043    0.652736
       f1    0.538922    0.664671    0.423819    0.571524


### Gliner
https://huggingface.co/urchade/gliner_multi

In [40]:
from gliner import GLiNER
model = GLiNER.from_pretrained("urchade/gliner_multi")

pytorch_model.bin:   0%|          | 0.00/1.17G [00:00<?, ?B/s]

gliner_config.json:   0%|          | 0.00/734 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/52.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/579 [00:00<?, ?B/s]

spm.model:   0%|          | 0.00/4.31M [00:00<?, ?B/s]

/nlp/projekty/gazetteer_ner/miniconda3/envs/dp/lib/python3.10/site-packages/transformers/convert_slow_tokenizer.py:550: UserWarning: The sentencepiece tokenizer that you are converting to a fast tokenizer uses the byte fallback option which is not implemented in the fast tokenizers. In practice this means that the fast version of the tokenizer can produce unknown tokens whereas the sentencepiece version would have converted these unknown tokens into a sequence of byte tokens matching the original piece of text.
  warnings.warn(


pytorch_model.bin:   0%|          | 0.00/1.33G [00:00<?, ?B/s]

In [41]:
def gliner_ger_ner_tag(text, word):
    words = word.split(" ")
    text = str(text)
    labels = {"person": "PER", "location": "LOC", "organization": "ORG"}
    for label in labels.keys():
        if label in text:
            if text not in words[0]:
                return "I-" + labels[label]
            return "B-" + labels[label]
def process_predictions_gliner(prediction, mid_result_for_word, label2id, sentence_counter, word):
    if  prediction["start"] > sentence_counter and prediction["end"] <= sentence_counter + len(word) + 1:
        score = mid_result_for_word[label2id.get(gliner_ger_ner_tag(prediction["label"], word), 0)]
        mid_result_for_word[label2id.get(gliner_ger_ner_tag(prediction["label"], word), 0)] = score +  prediction["score"]
    return mid_result_for_word
def predict_gliner(text):
    return model.predict_entities(text, ["person", "location", "organization"])

In [42]:
results, results_by_tag, data_for_cm = evaluate_test_model(None, None, dataset["test"], id2label, process_predictions_gliner, predict_gliner)

  0%|          | 0/900 [00:00<?, ?it/s]

100%|██████████| 900/900 [02:09<00:00,  6.94it/s]


In [43]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,4649706457925636; 0,5025440313111547; 0,450880626223092; 0,4908023483365949]
   Metric    ent_type     partial      strict       exact
  correct  594.000000  627.000000  576.000000  627.000000
incorrect   63.000000    0.000000   81.000000   30.000000
  partial    0.000000   30.000000    0.000000    0.000000
   missed  693.000000  693.000000  693.000000  693.000000
 spurious  548.000000  548.000000  548.000000  548.000000
 possible 1350.000000 1350.000000 1350.000000 1350.000000
   actual 1205.000000 1205.000000 1205.000000 1205.000000
precision    0.492946    0.532780    0.478008    0.520332
   recall    0.440000    0.475556    0.426667    0.464444
       f1    0.464971    0.502544    0.450881    0.490802


In [44]:
model = GLiNER.from_pretrained("urchade/gliner_largev2")
results, results_by_tag, data_for_cm = evaluate_test_model(None, None, dataset["test"], id2label, process_predictions_gliner, predict_gliner)

pytorch_model.bin:   0%|          | 0.00/1.84G [00:00<?, ?B/s]

gliner_config.json:   0%|          | 0.00/474 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/52.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/580 [00:00<?, ?B/s]

spm.model:   0%|          | 0.00/2.46M [00:00<?, ?B/s]

/nlp/projekty/gazetteer_ner/miniconda3/envs/dp/lib/python3.10/site-packages/transformers/convert_slow_tokenizer.py:550: UserWarning: The sentencepiece tokenizer that you are converting to a fast tokenizer uses the byte fallback option which is not implemented in the fast tokenizers. In practice this means that the fast version of the tokenizer can produce unknown tokens whereas the sentencepiece version would have converted these unknown tokens into a sequence of byte tokens matching the original piece of text.
  warnings.warn(


pytorch_model.bin:   0%|          | 0.00/874M [00:00<?, ?B/s]

100%|██████████| 900/900 [06:52<00:00,  2.18it/s]


In [45]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,4350721420643729; 0,47058823529411764; 0,42397336293007776; 0,46059933407325193]
   Metric    ent_type     partial      strict       exact
  correct  392.000000  415.000000  382.000000  415.000000
incorrect   41.000000    0.000000   51.000000   18.000000
  partial    0.000000   18.000000    0.000000    0.000000
   missed  695.000000  695.000000  695.000000  695.000000
 spurious  241.000000  241.000000  241.000000  241.000000
 possible 1128.000000 1128.000000 1128.000000 1128.000000
   actual  674.000000  674.000000  674.000000  674.000000
precision    0.581602    0.629080    0.566766    0.615727
   recall    0.347518    0.375887    0.338652    0.367908
       f1    0.435072    0.470588    0.423973    0.460599


### crabz/slovakbert-ner
https://huggingface.co/crabz/slovakbert-ner

In [10]:
def slovak_get_tag(tag):
    ner_map = {0: '0', 1: 'B-PER', 2: 'I-PER', 3: 'B-ORG', 4: 'I-ORG', 5: 'B-LOC', 6: 'I-LOC'}
    return ner_map.get(tag, "0")
def slovak_process_predictions(prediction, mid_result_for_word, label2id, sentence_counter, word):
    if  prediction["start"] > sentence_counter and prediction["end"] <= sentence_counter + len(word) + 1:
        score = mid_result_for_word[label2id.get(slovak_get_tag(prediction["entity"]), 0)]
        mid_result_for_word[label2id.get(slovak_get_tag(prediction["entity"]), 0)] = score +  prediction["score"]
    return mid_result_for_word

In [11]:
model_name = "crabz/slovakbert-ner"
tokenizer = AutoTokenizer.from_pretrained(model_name)
dataset = tokenize_dataset(tokenizer)
model = AutoModelForTokenClassification.from_pretrained(model_name).to("cuda")
results, results_by_tag, data_for_cm = evaluate_test_model(model, tokenizer, dataset["test"], id2label, slovak_process_predictions)

Map:   0%|          | 0/7193 [00:00<?, ? examples/s]

Map:   0%|          | 0/899 [00:00<?, ? examples/s]

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

100%|██████████| 900/900 [00:58<00:00, 15.35it/s]


In [12]:
x, y = get_result_as_tables(results, results_by_tag)
print(x)

[0,6438314640800241; 0,6832373446498939; 0,5704759017884208; 0,6317065777508335]
   Metric    ent_type     partial      strict       exact
  correct 1062.000000 1042.000000  941.000000 1042.000000
incorrect  150.000000    0.000000  271.000000  170.000000
  partial    0.000000  170.000000    0.000000    0.000000
   missed  139.000000  139.000000  139.000000  139.000000
 spurious  736.000000  736.000000  736.000000  736.000000
 possible 1351.000000 1351.000000 1351.000000 1351.000000
   actual 1948.000000 1948.000000 1948.000000 1948.000000
precision    0.545175    0.578542    0.483060    0.534908
   recall    0.786084    0.834197    0.696521    0.771281
       f1    0.643831    0.683237    0.570476    0.631707
